##Validando a SparkSession

In [0]:
spark

###Mostrando os pontos de montagem no cluster Databricks

In [0]:
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /Volumes UnityCatalogVolumes /mnt/datalake7a68c04c876ba15d/bronze wasbs://bronze@datalake7a68c04c876ba15d.blob.core.windows.net /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /databricks/mlflow-registry databricks/mlflow-registry /mnt/datalake7a68c04c876ba15d/silver wasbs://silver@datalake7a68c04c876ba15d.blob.core.windows.net /mnt/datalake7a68c04c876ba15d/gold wasbs://gold@datalake7a68c04c876ba15d.blob.core.windows.net /Volume DbfsReserved /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

### Acessando nome da Storage Account

In [0]:
storageAccountName = "datalake7a68c04c876ba15d"

###Desmontando os pontos de montagem não utilizados

In [0]:
dbutils.fs.unmount(f'/mnt/{storageAccountName}/bronze')

/mnt/datalake7a68c04c876ba15d/bronze has been unmounted.


True

###Mostrando os pontos de montagem no cluster Databricks

In [0]:
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /Volumes UnityCatalogVolumes /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /databricks/mlflow-registry databricks/mlflow-registry /mnt/datalake7a68c04c876ba15d/silver wasbs://silver@datalake7a68c04c876ba15d.blob.core.windows.net /mnt/datalake7a68c04c876ba15d/gold wasbs://gold@datalake7a68c04c876ba15d.blob.core.windows.net /Volume DbfsReserved /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

### Mostrando todos os arquivos da camada silver

In [0]:
display(dbutils.fs.ls(f"/mnt/{storageAccountName}/silver"))

path name size modificationTime dbfs:/mnt/datalake7a68c04c876ba15d/silver/agendamentos/ agendamentos/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/silver/cargas/ cargas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/silver/clientes/ clientes/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/silver/motoristas/ motoristas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/silver/rotas/ rotas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/silver/veiculos/ veiculos/ 0 0

###Gerando um dataframe dos delta lake no container bronze do Azure Data Lake Storage

In [0]:
df_agendamentos = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/agendamentos")
df_cargas = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/cargas")
df_clientes = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/clientes")
df_motoristas = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/motoristas")
df_rotas = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/rotas")
df_veiculos = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/veiculos")

##Criando tabelas dimensão


### Agendamentos

#### Apagando o arquivo já criado se necessário

In [0]:
# %sql
# DROP TABLE IF EXISTS dim_agendamentos;

In [0]:
# Verificar se o diretório não está vazio
# directory = "/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos"
# files = dbutils.fs.ls(directory)

# if files:
#    print(f"O diretório {directory} não está vazio. Removendo arquivos...")
#    for file in files:
#         try:
#             dbutils.fs.rm(file.path, True)
#             print(f"Arquivo {file.path} removido com sucesso.")
#         except Exception as e:
#             print(f"Erro ao remover o arquivo {file.path}: {e}")
# else:
#     print(f"O diretório {directory} está vazio ou não existe.")


O diretório /mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos não está vazio. Removendo arquivos...
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos/_delta_log/ removido com sucesso.
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos/part-00000-acf0734e-4f15-4bc6-bcac-7cb80047800a-c000.snappy.parquet removido com sucesso.


In [0]:
# BrunoSupriano: O comando acima foi criado com a intenção de automatizar a pipeline, se tiver arquivos dentro de dim agendamento ele exclui
# O comando abaixo é o mesmo que o de cima so que manual

com.databricks.sql.transaction.tahoe.DeltaFileNotFoundException: [DELTA_FILE_NOT_FOUND] File path /mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos
	at com.databricks.sql.transaction.tahoe.DeltaErrorsBase.fileNotFoundException(DeltaErrors.scala:504)
	at com.databricks.sql.transaction.tahoe.DeltaErrorsBase.fileNotFoundException$(DeltaErrors.scala:501)
	at com.databricks.sql.transaction.tahoe.DeltaErrors$.fileNotFoundException(DeltaErrors.scala:3323)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaDetailCommand.$anonfun$run$3(DescribeDeltaDetailsCommand.scala:113)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLogging.withOperationTypeTag(DeltaLogging.scala:225)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLogging.withOperationTypeTag$(DeltaLogging.scala:212)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaDetailCommand.withOperationTypeTag(DescribeDeltaDetailsCommand.scala:77)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLoggin

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos")
# for file in files:
#      dbutils.fs.rm(file.path, True) # Rodar esse e o debaixo se der erro de schema (não rodar se não der, só acontece quando muda as colunas da tabela no sql)

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-4495104486183831>, line 1
----> 1 files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos")
      2 for file in files:
      3      dbutils.fs.rm(file.path, True)

File /databricks/python_shell/dbruntime/dbutils.py:378, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    376 exc.__context__ = None
    377 exc.__cause__ = None
--> 378 raise exc

ExecutionError: An error occurred while calling o1818.ls.
: java.io.FileNotFoundException: No such file or directory /mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos
	at com.databricks.backend.daemon.data.client.DBFSV2.$anonfun$listStatus$2(DatabricksFileSystemV2.scala:135)
	at com.databricks.s3a.S3AExceptionUtils$.convertAWSExceptionToJavaIOException(DatabricksStreamUtils.scala:66)
	at com.databricks.backend.

In [0]:
#  %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos 

com.databricks.sql.transaction.tahoe.DeltaFileNotFoundException: [DELTA_FILE_NOT_FOUND] File path /mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos
	at com.databricks.sql.transaction.tahoe.DeltaErrorsBase.fileNotFoundException(DeltaErrors.scala:504)
	at com.databricks.sql.transaction.tahoe.DeltaErrorsBase.fileNotFoundException$(DeltaErrors.scala:501)
	at com.databricks.sql.transaction.tahoe.DeltaErrors$.fileNotFoundException(DeltaErrors.scala:3323)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaDetailCommand.$anonfun$run$3(DescribeDeltaDetailsCommand.scala:113)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLogging.withOperationTypeTag(DeltaLogging.scala:225)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLogging.withOperationTypeTag$(DeltaLogging.scala:212)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaDetailCommand.withOperationTypeTag(DescribeDeltaDetailsCommand.scala:77)
	at com.databricks.sql.transaction.tahoe.metering.DeltaLoggin

In [0]:
%sql
CREATE TABLE IF NOT EXISTS dim_agendamentos (
    sk_agendamentos BIGINT GENERATED BY DEFAULT AS IDENTITY,
    data_hora_coleta DATE,
    data_hora_entrega DATE,
    veiculo_id INT,
    carga_id INT
)
USING delta
LOCATION '/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos';

In [0]:
df_agendamentos.createOrReplaceTempView("temp_agendamentos")

In [0]:
%sql
MERGE INTO dim_agendamentos AS da
USING temp_agendamentos AS ta
ON da.veiculo_id = ta.codigo_veiculo AND da.carga_id = ta.codigo_carga
WHEN MATCHED AND (
    da.data_hora_coleta <> ta.data_hora_coleta OR 
    da.data_hora_entrega <> ta.data_hora_entrega
) THEN
  UPDATE SET 
    da.data_hora_coleta = ta.data_hora_coleta,
    da.data_hora_entrega = ta.data_hora_entrega,
    da.veiculo_id = ta.codigo_veiculo,
    da.carga_id = ta.codigo_carga
WHEN NOT MATCHED THEN
  INSERT (
    data_hora_coleta, data_hora_entrega, veiculo_id, carga_id
  )
  VALUES (
    ta.data_hora_coleta, ta.data_hora_entrega, ta.codigo_veiculo, ta.codigo_carga
  );


num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 0 0 0 0

### Cargas

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# drop table if exists dim_cargas;

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_cargas")
# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
#  %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_cargas

res11: Boolean = true

In [0]:
df_cargas.columns

['codigo_carga',
 'tipo_carga',
 'peso_carga',
 'comprimento',
 'largura',
 'altura',
 'data_entrega_prevista',
 'data_hora_bronze',
 'nome_arquivo',
 'data_hora_silver']

#### Criando tabela

In [0]:
%sql

CREATE TABLE IF NOT EXISTS dim_cargas (
   sk_cargas BIGINT GENERATED BY DEFAULT AS IDENTITY,
   codigo_carga BIGINT,
   tipo_carga VARCHAR(50),
   peso_carga DECIMAL(10, 2),
   comprimento DECIMAL(10, 2),
   largura DECIMAL(10, 2),
   altura DECIMAL(10, 2),
   data_entrega_prevista DATE
)
USING delta
LOCATION  '/mnt/datalake7a68c04c876ba15d/gold/dim_cargas';

In [0]:
df_cargas.createOrReplaceTempView("temp_cargas")

In [0]:
%sql
MERGE INTO dim_cargas AS dim
USING temp_cargas AS temp
ON dim.codigo_carga = temp.codigo_carga 
WHEN MATCHED AND (dim.tipo_carga <> temp.tipo_carga OR dim.peso_carga <> temp.peso_carga OR dim.comprimento <> temp.comprimento OR dim.largura <> temp.largura OR dim.altura <> temp.altura OR dim.data_entrega_prevista <> temp.data_entrega_prevista) THEN
  UPDATE SET 
    dim.tipo_carga = temp.tipo_carga,
    dim.peso_carga = temp.peso_carga,
    dim.comprimento = temp.comprimento,
    dim.largura = temp.largura,
    dim.altura = temp.altura,
    dim.data_entrega_prevista = temp.data_entrega_prevista
WHEN NOT MATCHED THEN
  INSERT (codigo_carga, tipo_carga, peso_carga, comprimento, largura, altura, data_entrega_prevista)
  VALUES (temp.codigo_carga, temp.tipo_carga, temp.peso_carga, temp.comprimento, temp.largura, temp.altura, temp.data_entrega_prevista);

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 10000 0 0 10000

In [0]:
%sql
SELECT * FROM dim_cargas LIMIT 5

sk_cargas codigo_carga tipo_carga peso_carga comprimento largura altura data_entrega_prevista 1 1 Materiais de Construção 58.46 2.08 2.32 0.40 2023-07-19 2 2 Materiais de Construção 953.46 3.51 2.91 1.92 2019-03-30 3 3 Materiais de Construção 918.68 4.70 2.51 1.30 2021-06-06 4 4 Roupas 135.58 4.21 1.98 1.59 2024-10-21 5 5 Roupas 630.42 0.57 1.14 0.32 2022-07-02

### Veículos

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# drop table if exists dim_veiculos

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_veiculos")

# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
# %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_veiculos

res2: Boolean = true

#### Criando tabela

In [0]:
%sql

CREATE TABLE IF NOT EXISTS dim_veiculos (
   sk_veiculos BIGINT GENERATED BY DEFAULT AS IDENTITY,
   codigo_veiculo BIGINT,
   tipo_veiculo VARCHAR(50),
   data_aquisicao DATE,
   estado_veiculo VARCHAR(50),
   placa_veiculo VARCHAR(10)
)
USING delta
LOCATION  '/mnt/datalake7a68c04c876ba15d/gold/dim_veiculos';

In [0]:
df_veiculos.createOrReplaceTempView("temp_veiculos")

In [0]:
df_veiculos.columns

['codigo_veiculo',
 'tipo_veiculo',
 'data_aquisicao',
 'estado_veiculo',
 'placa_veiculo',
 'codigo_motorista',
 'data_hora_bronze',
 'nome_arquivo',
 'data_hora_silver']

In [0]:
%sql
MERGE INTO dim_veiculos AS dim
USING temp_veiculos AS temp
ON dim.codigo_veiculo = temp.codigo_veiculo 
WHEN MATCHED AND (dim.tipo_veiculo <> temp.tipo_veiculo OR dim.data_aquisicao <> temp.data_aquisicao OR dim.estado_veiculo <> temp.estado_veiculo OR dim.placa_veiculo <> temp.placa_veiculo) THEN
  UPDATE SET 
    dim.tipo_veiculo = temp.tipo_veiculo,
    dim.data_aquisicao = temp.data_aquisicao,
    dim.estado_veiculo = temp.estado_veiculo,
    dim.placa_veiculo = temp.placa_veiculo

WHEN NOT MATCHED THEN
  INSERT (codigo_veiculo, tipo_veiculo, data_aquisicao, estado_veiculo, placa_veiculo)
  VALUES (temp.codigo_veiculo,temp.tipo_veiculo, temp.data_aquisicao, temp.estado_veiculo, temp.placa_veiculo);

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 0 0 0 0

In [0]:
display(dbutils.fs.ls(f"/mnt/{storageAccountName}/gold"))

path name size modificationTime dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_agendamentos/ dim_agendamentos/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_cargas/ dim_cargas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_clientes/ dim_clientes/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_motoristas/ dim_motoristas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_rotas/ dim_rotas/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_tempo/ dim_tempo/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_veiculos/ dim_veiculos/ 0 0 dbfs:/mnt/datalake7a68c04c876ba15d/gold/fato_entregas/ fato_entregas/ 0 0

### Motoristas

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# drop table if exists dim_motoristas

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_motoristas")

# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
# %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_motoristas

res3: Boolean = true

#### Criando tabela

In [0]:
%sql

CREATE TABLE IF NOT EXISTS dim_motoristas (
   sk_motoristas BIGINT GENERATED BY DEFAULT AS IDENTITY,
   codigo_motorista BIGINT,
   nome VARCHAR(255),
   telefone VARCHAR(15),
   numero_carteira VARCHAR(10),
   data_contratacao DATE,
   categoria_carteira VARCHAR(30),
   status VARCHAR(30)
)
USING delta
LOCATION  '/mnt/datalake7a68c04c876ba15d/gold/dim_motoristas';

In [0]:
df_motoristas.createOrReplaceTempView("temp_motoristas")

In [0]:
%sql
MERGE INTO dim_motoristas AS dim
USING temp_motoristas AS temp
ON dim.codigo_motorista = temp.codigo_motorista 
WHEN MATCHED AND (dim.nome <> temp.nome OR dim.telefone <> temp.telefone OR dim.numero_carteira <> temp.numero_carteira OR dim.data_contratacao <> temp.data_contratacao OR dim.categoria_carteira <> temp.categoria_carteira OR dim.status <> temp.status) THEN
  UPDATE SET 
    dim.nome = temp.nome,
    dim.telefone = temp.telefone,
    dim.numero_carteira = temp.numero_carteira,
    dim.data_contratacao = temp.data_contratacao,
    dim.categoria_carteira = temp.categoria_carteira,
    dim.status = temp.status

WHEN NOT MATCHED THEN
  INSERT (codigo_motorista, nome, telefone, numero_carteira, data_contratacao, categoria_carteira, status)
  VALUES (temp.codigo_motorista,temp.nome, temp.telefone, temp.numero_carteira, temp.data_contratacao, temp.categoria_carteira, temp.status);

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 0 0 0 0

In [0]:
%sql

select * from dim_motoristas LIMIT 5

sk_motoristas codigo_motorista nome telefone numero_carteira data_contratacao categoria_carteira status 1 1 Srta. Stephany Jesus 02104651614 73231 2020-11-09 D Afastado 2 2 Dr. Juan Cavalcanti 5508120031041 75882 2023-02-06 D Ativo 3 3 Anthony Vieira 552135315362 83325 2022-03-24 D Ativo 4 4 Danilo Cavalcanti 7123723313 61690 2021-03-01 D Inativo 5 5 Fernanda Pacheco 555183607614 86594 2021-07-22 D Inativo

### Rotas

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# drop table if exists dim_rotas

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_rotas")

# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
# %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_rotas

res5: Boolean = true

#### Criando tabela

In [0]:
%sql

CREATE TABLE IF NOT EXISTS dim_rotas (
   sk_rotas BIGINT GENERATED BY DEFAULT AS IDENTITY,
   codigo_rota BIGINT,
   origem CHAR(2),
   destino CHAR(2),
   tempo_estimado INT
)
USING delta
LOCATION  '/mnt/datalake7a68c04c876ba15d/gold/dim_rotas';


In [0]:
df_rotas.createOrReplaceTempView("temp_rotas")

In [0]:
%sql
select * from temp_rotas limit 4

codigo_rota origem destino distancia tempo_estimado data_hora_bronze nome_arquivo data_hora_silver 1 MG SP 944.66 1138 2024-06-28T16:57:03.629Z rotas 2024-06-28T17:03:41.932Z 2 PA AL 1403.32 338 2024-06-28T16:57:03.629Z rotas 2024-06-28T17:03:41.932Z 3 GO PE 177.2 336 2024-06-28T16:57:03.629Z rotas 2024-06-28T17:03:41.932Z 4 PR MG 1541.26 289 2024-06-28T16:57:03.629Z rotas 2024-06-28T17:03:41.932Z

In [0]:
%sql
MERGE INTO dim_rotas AS dim
USING temp_rotas AS temp
ON dim.codigo_rota = temp.codigo_rota 
WHEN MATCHED AND (dim.origem <> temp.origem OR dim.destino <> temp.destino OR dim.tempo_estimado <> temp.tempo_estimado) THEN
  UPDATE SET 
    dim.origem = temp.origem,
    dim.destino = temp.destino,
    dim.tempo_estimado = temp.tempo_estimado

WHEN NOT MATCHED THEN
  INSERT (codigo_rota, origem, destino, tempo_estimado)
  VALUES (temp.codigo_rota,temp.origem, temp.destino, temp.tempo_estimado);

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 0 0 0 0

In [0]:
%sql
select * from dim_rotas limit 5

sk_rotas codigo_rota origem destino tempo_estimado 1 1 MG SP 1138 2 2 PA AL 338 3 3 GO PE 336 4 4 PR MG 289 5 5 SE TO 1083

### Clientes

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# DROP TABLE IF EXISTS dim_clientes

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_clientes")

# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
# %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_clientes

res6: Boolean = true

#### Criando tabela

In [0]:
%sql

CREATE TABLE IF NOT EXISTS dim_clientes (
   sk_clientes BIGINT GENERATED BY DEFAULT AS IDENTITY,
   codigo_cliente BIGINT,
   nome_cliente VARCHAR(255),
   contato_cliente VARCHAR(15),
   tipo_cliente VARCHAR(50),
   logradouro_cliente VARCHAR(100),
   numero_residencia_cliente VARCHAR(5),
   bairro_cliente VARCHAR(100),
   cep_cliente VARCHAR(10),
   cidade_cliente VARCHAR(100),
   uf_cliente CHAR(2)
)
USING delta
LOCATION  '/mnt/datalake7a68c04c876ba15d/gold/dim_clientes';

In [0]:
df_clientes.createOrReplaceTempView("temp_clientes")

In [0]:
df_clientes.columns

['codigo_cliente',
 'nome_cliente',
 'contato_cliente',
 'tipo_cliente',
 'data_hora_bronze',
 'nome_arquivo',
 'data_hora_silver',
 'logradouro_cliente',
 'numero_residencia_cliente',
 'bairro_cliente',
 'cep_cliente',
 'cidade_cliente',
 'uf_cliente']

In [0]:
%sql
MERGE INTO dim_clientes AS dim
USING temp_clientes AS temp
ON dim.codigo_cliente = temp.codigo_cliente 
WHEN MATCHED AND (dim.nome_cliente <> temp.nome_cliente OR dim.contato_cliente <> temp.contato_cliente OR dim.tipo_cliente <> temp.tipo_cliente OR dim.logradouro_cliente <> temp.logradouro_cliente OR dim.numero_residencia_cliente <> temp.numero_residencia_cliente OR dim.bairro_cliente <> temp.bairro_cliente OR dim.cep_cliente <> temp.cep_cliente OR dim.cidade_cliente <> temp.cidade_cliente OR dim.uf_cliente <> temp.uf_cliente ) THEN
  UPDATE SET 
    dim.nome_cliente = temp.nome_cliente,
    dim.contato_cliente = temp.contato_cliente,
    dim.tipo_cliente = temp.tipo_cliente,
    dim.logradouro_cliente = temp.logradouro_cliente,
    dim.numero_residencia_cliente = temp.numero_residencia_cliente,
    dim.bairro_cliente = temp.bairro_cliente,
    dim.cep_cliente = temp.cep_cliente,
    dim.cidade_cliente = temp.cidade_cliente,
    dim.uf_cliente = temp.uf_cliente

WHEN NOT MATCHED THEN
  INSERT (codigo_cliente, nome_cliente, contato_cliente, tipo_cliente, logradouro_cliente, numero_residencia_cliente, bairro_cliente, cep_cliente, cidade_cliente, uf_cliente)
  VALUES (temp.codigo_cliente,temp.nome_cliente, temp.contato_cliente, temp.tipo_cliente, temp.logradouro_cliente, temp.numero_residencia_cliente, temp.bairro_cliente, temp.cep_cliente, temp.cidade_cliente, temp.uf_cliente);

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 0 0 0 0

In [0]:
%sql
select * from dim_clientes LIMIT 5

sk_clientes codigo_cliente nome_cliente contato_cliente tipo_cliente logradouro_cliente numero_residencia_cliente bairro_cliente cep_cliente cidade_cliente uf_cliente 1 27 Ana Júlia Pires 552196837359 Pessoa Física Residencial Thomas Santos 63 Horto Florestal 00250402 Viana PA 2 30 Ágatha Viana 6186016419 Pessoa Jurídica Praia Olívia Pereira 58 Independência 01912633 Sousa do Sul SC 3 475 Ravy da Conceição 5508454122438 Pessoa Física Lago Milena Andrade 62 Renascença 39825177 Montenegro RS 4 965 Isabel da Conceição 8189596360 Pessoa Jurídica Fazenda Campos S/N Buritis 21120769 Pinto PA 5 1678 Bento Nascimento 08443026880 Pessoa Física Campo Rezende 88 Parque São Pedro 06069081 da Costa AC

### Tempo

#### Apagando arquivo já criado se necessário

In [0]:
# %sql
# drop table if exists dim_tempo

In [0]:
# files = dbutils.fs.ls("/mnt/datalake7a68c04c876ba15d/gold/dim_tempo")

# for file in files:
#      dbutils.fs.rm(file.path, True)

In [0]:
# %fs rm -r dbfs:/mnt/datalake7a68c04c876ba15d/gold/dim_tempo

res7: Boolean = true

#### Criando tabela

In [0]:
from pyspark.sql.functions import min, max, row_number
from pyspark.sql import Window

menor_data = df_agendamentos.agg(min("data_hora_coleta")).collect()[0][0]

maior_data = df_agendamentos.agg(max("data_hora_entrega")).collect()[0][0]

num_dias = spark.sql(f"SELECT datediff('{maior_data}', '{menor_data}')").collect()[0][0]

df_calendario = spark.range(0, num_dias + 1) \
    .selectExpr(f"date_add(to_date('{menor_data}'), CAST(id AS INT)) AS Data")

df_tempo = df_calendario.selectExpr(
    "Data AS data",
    "year(Data) AS ano",
    "month(Data) AS mes",
       "(CASE month(Data) \
        WHEN 1 THEN 'JANEIRO' \
        WHEN 2 THEN 'FEVEREIRO' \
        WHEN 3 THEN 'MARCO' \
        WHEN 4 THEN 'ABRIL' \
        WHEN 5 THEN 'MAIO' \
        WHEN 6 THEN 'JUNHO' \
        WHEN 7 THEN 'JULHO' \
        WHEN 8 THEN 'AGOSTO' \
        WHEN 9 THEN 'SETEMBRO' \
        WHEN 10 THEN 'OUTUBRO' \
        WHEN 11 THEN 'NOVEMBRO' \
        WHEN 12 THEN 'DEZEMBRO' \
    END) AS nome_mes",
    "day(Data) AS dia",
    "(CASE dayofweek(Data) \
        WHEN 1 THEN 'DOMINGO' \
        WHEN 2 THEN 'SEGUNDA-FEIRA' \
        WHEN 3 THEN 'TERCA-FEIRA' \
        WHEN 4 THEN 'QUARTA-FEIRA' \
        WHEN 5 THEN 'QUINTA-FEIRA' \
        WHEN 6 THEN 'SEXTA-FEIRA' \
        WHEN 7 THEN 'SABADO' \
    END) AS nome_dia_semana",
    "dayofweek(Data) AS numero_dia_semana"
)

windowSpec = Window.orderBy("data")
df_tempo = df_tempo.withColumn("sk_tempo", row_number().over(windowSpec))

df_tempo.write.mode("overwrite") \
    .option("path", f"/mnt/{storageAccountName}/gold/dim_tempo") \
    .saveAsTable("dim_tempo", format="delta")

In [0]:
%sql
select * from dim_tempo limit 5

data ano mes nome_mes dia nome_dia_semana numero_dia_semana sk_tempo 2019-01-01 2019 1 JANEIRO 1 TERCA-FEIRA 3 1 2019-01-02 2019 1 JANEIRO 2 QUARTA-FEIRA 4 2 2019-01-03 2019 1 JANEIRO 3 QUINTA-FEIRA 5 3 2019-01-04 2019 1 JANEIRO 4 SEXTA-FEIRA 6 4 2019-01-05 2019 1 JANEIRO 5 SABADO 7 5

## Criando tabela Fato

### Entregas

#### Apagando arquivo já criado se necessário

In [0]:
%sql
drop table if exists fato_entregas

In [0]:
# Verificar se o diretório não está vazio
directory = "/mnt/datalake7a68c04c876ba15d/gold/fato_entregas"
files = dbutils.fs.ls(directory)

if files:
   print(f"O diretório {directory} não está vazio. Removendo arquivos...")
   for file in files:
        try:
            dbutils.fs.rm(file.path, True)
            print(f"Arquivo {file.path} removido com sucesso.")
        except Exception as e:
            print(f"Erro ao remover o arquivo {file.path}: {e}")
else:
    print(f"O diretório {directory} está vazio ou não existe.")


O diretório /mnt/datalake7a68c04c876ba15d/gold/fato_entregas não está vazio. Removendo arquivos...
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/fato_entregas/_delta_log/ removido com sucesso.
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/fato_entregas/part-00000-1175747c-537a-440e-bec4-0c1b4a3469ff-c000.snappy.parquet removido com sucesso.
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/fato_entregas/part-00000-9c25fb21-0fc3-4621-892d-a1e39c1a1378-c000.snappy.parquet removido com sucesso.
Arquivo dbfs:/mnt/datalake7a68c04c876ba15d/gold/fato_entregas/part-00000-e8127915-db36-4a07-8d4d-59d9e209f3c5-c000.snappy.parquet removido com sucesso.


#### Criando tabela

In [0]:
%sql
CREATE TABLE IF NOT EXISTS fato_entregas (
   sk_entrega BIGINT GENERATED BY DEFAULT AS IDENTITY,
   fk_cargas BIGINT,
   fk_veiculos BIGINT,
   fk_motoristas BIGINT,
   fk_rotas BIGINT,
   fk_clientes BIGINT,
   fk_data_coleta BIGINT,
   fk_data_entrega BIGINT,
   fk_data_prevista_entrega BIGINT,
   distancia_percorrida NUMERIC(10,2),
   tempo_entrega NUMERIC(10,2),
   volume_carga NUMERIC(10,2)
)
USING delta
LOCATION '/mnt/datalake7a68c04c876ba15d/gold/fato_entregas';

##### Adicionando tempo_entrega e alterando data_hora para somente data

In [0]:
from pyspark.sql.types import TimestampType
from pyspark.sql.functions import unix_timestamp, col, to_date

df_agendamentos_fato = df_agendamentos \
  .withColumn("data_hora_coleta" ,
              df_agendamentos["data_hora_coleta"]
              .cast(TimestampType()))   \
  .withColumn("data_hora_entrega",
              df_agendamentos["data_hora_entrega"]
              .cast(TimestampType()))


df_agendamentos_fato = df_agendamentos_fato.withColumn("coleta_segundos", unix_timestamp(col("data_hora_coleta"))) \
    .withColumn("entrega_segundos", unix_timestamp(col("data_hora_entrega"))) \
        .withColumn("diferenca_segundos", col("entrega_segundos") - col("coleta_segundos"))

df_agendamentos_fato = df_agendamentos_fato.withColumn("tempo_entrega", col("diferenca_segundos") / 3600)



df_agendamentos_fato = df_agendamentos_fato.withColumn("data_coleta", to_date("data_hora_coleta")) \
  .withColumn("data_entrega", to_date("data_hora_entrega"))

df_agendamentos_fato = df_agendamentos_fato.drop("entrega_segundos", "diferenca_segundos", "coleta_segundos", "data_hora_entrega", "data_hora_coleta")

df_agendamentos_fato.display()

codigo_agendamento codigo_veiculo codigo_carga codigo_rota codigo_cliente data_hora_bronze nome_arquivo data_hora_silver tempo_entrega data_coleta data_entrega 1 631 3042 1728 1471 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 552.0 2019-10-22 2019-11-14 2 6028 1649 977 8136 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 576.0 2024-01-31 2024-02-24 3 1227 4382 524 6560 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 144.0 2023-08-01 2023-08-07 4 131 6561 8786 781 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 144.0 2020-07-12 2020-07-18 5 2260 5315 5068 1075 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 48.0 2021-12-21 2021-12-23 6 8750 4505 1019 346 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 96.0 2021-09-11 2021-09-15 7 4400 9879 1682 9891 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 528.0 2022-11-28 2022-12-20 8 6369 2956 9396 3791 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 312.0 2023-09-25 2023-10-08 9 847 313 469 7102 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 192.0 2019-07-25 2019-08-02 10 8200 6688 9044 3516 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 552.0 2019-03-04 2019-03-27 11 8689 3483 3096 5563 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 672.0 2024-01-06 2024-02-03 12 4380 3901 9613 9544 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 192.0 2021-08-06 2021-08-14 13 4773 9616 464 3054 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 576.0 2023-07-29 2023-08-22 14 342 5488 6820 4446 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 96.0 2019-01-05 2019-01-09 15 9157 8271 2746 2625 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 480.0 2021-09-02 2021-09-22 16 2379 7603 8253 1151 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 72.0 2023-04-30 2023-05-03 17 6455 2983 3008 6076 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 528.0 2020-05-16 2020-06-07 18 6177 4024 5367 354 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 576.0 2024-09-02 2024-09-26 19 8663 3986 8879 4886 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 696.0 2024-05-29 2024-06-27 20 8264 208 9386 6023 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 696.0 2019-03-09 2019-04-07 21 222 9431 191 7239 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 264.0 2019-02-25 2019-03-08 22 7533 8974 8215 661 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 96.0 2022-04-01 2022-04-05 23 94 1613 6152 5455 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 312.0 2024-08-19 2024-09-01 24 2671 6365 232 8072 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 240.0 2021-04-15 2021-04-25 25 6779 4436 3056 7071 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 384.0 2020-04-19 2020-05-05 26 2903 4178 3451 9362 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 144.0 2021-07-13 2021-07-19 27 6139 3204 686 3106 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 96.0 2019-03-05 2019-03-09 28 621 1462 3101 3897 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 408.0 2020-04-30 2020-05-17 29 7443 6445 2374 5404 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 264.0 2021-08-17 2021-08-28 30 593 3663 5430 9370 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 240.0 2021-12-22 2022-01-01 31 7298 4373 7085 8218 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 696.0 2020-05-25 2020-06-23 32 2338 32 9367 1346 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 504.0 2020-05-20 2020-06-10 33 9771 505 6504 1680 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 504.0 2020-04-24 2020-05-15 34 848 9269 1787 3416 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 624.0 2021-10-03 2021-10-29 35 6343 8223 214 384 2024-06-28T16:55:1

##### Adicionando codigo_motorista ao DataFrame agendamentos

In [0]:
df_agendamentos_fato = df_agendamentos_fato.join(
    df_veiculos.select("codigo_veiculo", "codigo_motorista"),
    on="codigo_veiculo",
    how="left"
)

##### Populando a tabela fato

In [0]:
df_agendamentos_fato.createOrReplaceTempView("temp_agendamentos_fato")

In [0]:
%sql
SELECT * FROM temp_agendamentos_fato limit 3

codigo_veiculo codigo_agendamento codigo_carga codigo_rota codigo_cliente data_hora_bronze nome_arquivo data_hora_silver tempo_entrega data_coleta data_entrega codigo_motorista 631 1 3042 1728 1471 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 552.0 2019-10-22 2019-11-14 2510 6028 2 1649 977 8136 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 576.0 2024-01-31 2024-02-24 8290 1227 3 4382 524 6560 2024-06-28T16:55:13.033Z agendamentos 2024-06-28T17:01:52.05Z 144.0 2023-08-01 2023-08-07 9204

In [0]:
%sql
with cte as (
	select tc.codigo_carga, tem.sk_tempo 
	from temp_cargas tc 
	inner join dim_tempo tem 
	on tc.data_entrega_prevista = tem.data
)
insert into fato_entregas (
	fk_cargas, 
	fk_veiculos, 
	fk_motoristas, 
	fk_rotas, 
	fk_clientes, 
	fk_data_coleta, 
	fk_data_entrega, 
	fk_data_prevista_entrega, 
	distancia_percorrida, 
	tempo_entrega,
	volume_carga
	)
select 	
		car.sk_cargas,
		ve.sk_veiculos,
		mo.sk_motoristas,
		ro.sk_rotas,
		cli.sk_clientes,
		coleta.sk_tempo,
		entrega.sk_tempo,
		cte.sk_tempo,
		tr.distancia,
		fato.tempo_entrega,
		car.comprimento * car.altura * car.largura
from temp_agendamentos_fato fato
	   inner join dim_cargas car
	     on car.codigo_carga = fato.codigo_carga
       inner join dim_veiculos ve
	     on ve.codigo_veiculo = fato.codigo_veiculo
	   inner join dim_motoristas mo
	     on mo.codigo_motorista = fato.codigo_motorista
	   inner join dim_rotas ro
	   	 on ro.codigo_rota = fato.codigo_rota
	   inner join dim_clientes cli
	     on cli.codigo_cliente = fato.codigo_cliente
	   inner join cte
	   	 on cte.codigo_carga = fato.codigo_carga
	   inner join dim_tempo coleta
	     on coleta.data = fato.data_coleta
	   inner join dim_tempo entrega
	     on entrega.data = fato.data_entrega
	   inner join temp_rotas tr
	     on tr.codigo_rota = fato.codigo_rota
	   

num_affected_rows num_inserted_rows 10000 10000

In [0]:
%sql
SELECT COUNT(*) FROM fato_entregas

count(1) 10000